### 1. Objective
The objective of the notebook is to perform feature selection and get the significant & important features using lasso implemented with SciPy. The notebook performs the following key steps
 - Builds Lasso model for different combinations of alpha and gamma hyperparameters provided in the config and exports the coefficients of all combinations
 - Calculates contributions of the base and incremental variables for all the iterations
 - Exports the coefficients and contributions for all the iterations

### 2. Imports

In [0]:
import pandas as  pd
import numpy as np
import datetime as dt
import os
import logging
import scipy
from datetime import datetime
import sys
#import joblib
import multiprocessing
import random
import functools
from sklearn.metrics import mean_absolute_error,mean_squared_error
from sklearn.preprocessing import MinMaxScaler, StandardScaler
# import joblib
import sys, traceback

import contextlib
from scipy.optimize import minimize
# from pyspark.context import SparkContext
# import pyspark.sql.functions as F
# from pyspark.sql.types import *
# from pyspark.sql.window import Window
# from pyspark.sql.functions import *
# from pyspark.sql.types import NumericType
# from pyspark.context import SparkContext
# from pyspark.sql.session import SparkSession
from sklearn.model_selection import train_test_split

from snowflake.snowpark.context import get_active_session
from snowflake.snowpark import functions as F
from snowflake.snowpark.functions import col, count, sum as sum_, countDistinct, mean as mean_, round as round_, min as min_, max as max_, when, is_null, lit
session = get_active_session()

### 3. Setup environment

#### 3.1 Loading contribution calculation module

In [ ]:
import pandas as pd
import numpy as np
import shutil
import glob
import os
import re
import itertools
import json
import yaml
# import matplotlib.pyplot as plt
# import matplotlib.gridspec as gridspec
# from matplotlib.widgets import Slider, CheckButtons
import datetime as dt
#import libify
from itertools import product
import ast

In [ ]:
def contribution_cal_base_variable(model_coef,model_df,base_col_substr_order,idv_column,intercept_name,date_column,coef_col,Avg_Price_column,primary_key):
  
  # print(1)
  model_coef.rename(columns = {idv_column:'Variable'},inplace = True)

  #date column
  date=date_column
  #model_df.rename(columns = {'week_start_date':'Date'},inplace = True) ## Change here
  model_df[date] = pd.to_datetime(model_df[date])
  
  base_var = list(model_coef[(model_coef['Base_incr_comp'] == 'Base') & ((model_coef['Variable'] != intercept_name))]['Variable'])
  
  # SI_cols = [i for i in base_var if "Si_" in i ]
  # trend_cols = [i for i in base_var if "Trend_" in i ]
  # avg_search_rank_cols = [i for i in base_var if "Average_Organic_Search_" in i ]
  # baseprice_cols = ['Median_Baseprice_Log'] + [i for i in base_var if 'Median_Baseprice_Comp' in i]
  # feedback_col = [i for i in base_var if "Feedback_Avg_Rating" in i ]
  # covid_cols = [i for i in base_var if "Covid_" in i ]
  # base_var = baseprice_cols + covid_cols + avg_search_rank_cols + feedback_col  + SI_cols + trend_cols

  result_lists = []
  for substring in base_col_substr_order:
      result_list = [i for i in base_var if substring == i]
      result_lists.extend(result_list)
  # print(result_lists)
  base_var=result_lists.copy()
  #print("Base_Var list",base_var)
  price = Avg_Price_column ## Change here
  price_val = model_df[[price]]
  
  #model_df[["PPG_Cat", "PPG_MFG", "PPG_Item_No", "PPG_Description"]] = pd.DataFrame([["TEMP"]*4], index=model_df.index) ## change here
  overall_dt_dist_df, overall_qtr_dist_df, overall_yr_dist_df = get_var_contribution_wo_baseline_defined(model_df, model_coef, price_val,primary_key,all_df=None, var_col="Variable", coef_col=coef_col, intercept_name=intercept_name, base_var=base_var)
  # print(overall_dt_dist_df.columns)
  overall_yr_dist_df['Year'] = overall_yr_dist_df['Year'].astype(int)
  #overall_yr_dist_df['Year'] = np.where(overall_yr_dist_df['Year']==2019,2020,overall_yr_dist_df['Year']) ### since "2019-12-30" belongs to 2020
  overall_yr_dist_df = overall_yr_dist_df.groupby(['Year','model_coefficient_name']).agg(units=('units',np.sum)).reset_index()
  overall_yr_dist_df1 = overall_yr_dist_df[overall_yr_dist_df['model_coefficient_name']!= 'Predicted_sales']
  yearly_1 = overall_yr_dist_df1[['Year','units']].groupby(by=["Year"], as_index=False).agg(np.sum).rename(columns = {'units':"Yearly_Units"})
  overall_yr_dist_df1 = pd.merge(overall_yr_dist_df1,yearly_1,on = "Year",how = "left")
  overall_yr_dist_df1['units%'] = overall_yr_dist_df1['units']/overall_yr_dist_df1['Yearly_Units']*100

  #########Converting to Required Format
  dt_dist = pd.pivot_table(overall_dt_dist_df[[date,'model_coefficient_name','units']],index = [date_column],columns = "model_coefficient_name")
  # raise Exception(dt_dist.columns)
  dt_dist = pd.DataFrame(dt_dist).reset_index()
  dt_dist.columns = dt_dist.columns.droplevel(0) 
  # print(dt_dist.columns)
  a = [date_column]+list(dt_dist.columns[1:])
  dt_dist.columns = a
  # print(dt_dist.columns)

  year_dist = pd.pivot_table(overall_yr_dist_df[['Year','model_coefficient_name','units']],index = ["model_coefficient_name"],columns = "Year")
  year_dist = pd.DataFrame(year_dist).reset_index()
  year_dist.columns = year_dist.columns.droplevel(0) 
  # print(year_dist.columns)
  a = ["model_coefficient_name"]+list(year_dist.columns[1:])
  year_dist.columns = a
  # print(year_dist.columns)

  year_dist1 = pd.pivot_table(overall_yr_dist_df1[['Year','model_coefficient_name','units%']],index = ["model_coefficient_name"],columns = "Year")
  year_dist1 = pd.DataFrame(year_dist1).reset_index()
  year_dist1.columns = year_dist1.columns.droplevel(0) 
  # print(year_dist1.columns)
  a = ["model_coefficient_name"]+list(year_dist1.columns[1:])
  year_dist1.columns = a
  # print(year_dist1.columns)

  ########Lift Calculation
  aa = dt_dist.columns
  # raise Exception(aa)
  # logger.info('columns in cont calc are',aa)
#   print(aa)

  ### Competitor Discounts
  Comp = [i for i in aa if "Tpr_Discount_Comp" in i ] ## Change here
  # print("Comp",Comp)
  dt_dist['Comp'] = dt_dist[Comp].sum(axis = 1)
  ###Give tpr related Variables
  Inc_var=model_coef[(model_coef['Base_incr_comp']=='Increment_Act')]['Variable'].to_list()
#   print("Inc_var",Inc_var)
  Incremental=[i+"_contribution_impact" for i in Inc_var]
#   print("Inc_var",Incremental)
  dt_dist['Incremental'] = dt_dist[Incremental].sum(axis = 1)

  ###Give the remaining Base columns
  base=model_coef[(model_coef['Base_incr_comp']=='Base')]['Variable'].to_list()
  # raise Exception(base)
  base_others = model_coef[(model_coef['Base_incr_comp']=='Increment_Others')]['Variable'].to_list()
  base_others = [i for i in base_others if "Tpr_Discount_Comp" not in i]

  base=[i+"_contribution_base" for i in base] + [i+'_contribution_base' for i in base_others]
  base = [i for i in base if i != 'Intercept_contribution_impact']
  base = base + ['Intercept_contribution_base']
  # raise Exception(aa)

  dt_dist['Base'] = dt_dist[base].sum(axis = 1)

  # print("Total",len(Incremental+base))
  # print("Total",len(aa)-2)

  ######Adjusted Base
  dt_dist['Adj_Base'] = dt_dist['Base']
  dt_dist['Final_Base'] = np.where((dt_dist['Base']+dt_dist['Comp'])<0,dt_dist['Base'],dt_dist['Base']+dt_dist['Comp'])
  ## Add to incremental only if incremental present
  dt_dist['Final_Incremental'] = np.where((((dt_dist['Base']+dt_dist['Comp'])<0)&(dt_dist['Incremental']>0))
                                          ,dt_dist['Incremental']+dt_dist['Comp'],dt_dist['Incremental'])

  
  #dt_dist['Lift'] = dt_dist['Incremental']/((dt_dist['Base']+dt_dist['Comp']))
  dt_dist['Lift'] = dt_dist['Final_Incremental']/(dt_dist['Final_Base'])

  ### Calculating the contribution by type
  year_dist1['Type'] = np.where(year_dist1['model_coefficient_name'].isin(Comp),"Competitor",
                             np.where(year_dist1['model_coefficient_name'].isin(Incremental),"Incremental",
                                     np.where(year_dist1['model_coefficient_name'].isin(base),"Base","Remaining")))



##  IS REQUIRED??????
  ### Calculating the contribution
  year_dist2_base_comp = year_dist1[(year_dist1['Type']=="Base") | (year_dist1['Type']=="Competitor")]
  year_dist2_year_col = year_dist2_base_comp.columns.drop(['model_coefficient_name', 'Type'])

  year_dist2_dict_col = {}
  for i in year_dist2_year_col:
    year_dist2_dict_col[i] = 'contribution_'+ str(i)

  year_dist2_base_comp = year_dist2_base_comp.groupby(['Type']).agg(np.sum).reset_index()
  year_dist2_base_comp = year_dist2_base_comp.rename(columns = year_dist2_dict_col)  

  year_dist2_base_comp['model_coefficient_name'] = year_dist2_base_comp['Type']
  year_dist2_incr =  year_dist1[(year_dist1['Type']=="Incremental")]

  year_dist2_incr.rename(columns = year_dist2_dict_col,inplace = True)
  year_dist2 = pd.concat([year_dist2_base_comp,year_dist2_incr],ignore_index = True)
  first_column = year_dist2.pop('model_coefficient_name')
  year_dist2.insert(1, 'model_coefficient_name', first_column)


#   ### Lift by activity and year
  dt_dist['Year'] = dt_dist[date].dt.year
  

  
  df = dt_dist.melt(['Year',date], var_name='Variable', value_name='Value')
  df_Adj_Base= df[(df['Variable']=="Final_Base") & (df['Value']!=0)].reset_index(drop = True) #Adj_Base
  df_Adj_Base.rename(columns = {'Value':'Final_Base'},inplace = True)
  
  df_temp1 = df.copy()
  df = df[(df['Variable'].isin(Incremental)) & (df['Value']!=0)]
  df = pd.merge(df,df_Adj_Base[['Year',date,'Final_Base']],on = ['Year',date],how = "left")

  df1 = df.groupby(['Year','Variable']).agg(incr_sales = ("Value",np.sum),
                                            count = ("Value","count"),
                                            Final_Base = ("Final_Base",np.sum)
                                           ).reset_index() #Adj_Base
  # print(102)
  df1['Lift'] = (df1['incr_sales']/df1['Final_Base'])*100
  df2 = df1.pivot_table(index = ['Variable'],columns = 'Year',values = ['incr_sales','Final_Base','Lift','count']).reset_index()
  try:
    df2 = df2[['Variable', 'Lift', 'count', 'incr_sales', 'Final_Base']]
  except:
    print("got expection for this prod:",model_df[primary_key[0]].unique())
    # # df_temp1.display()
    # raise Exception("UPC",model_df['Product UPC'].unique(),"TPR values",model_df['TPR_finalized'].unique(),"incremental value",df_temp1[df_temp1['Variable'] == 'TPR_finalized_contribution_impact']['Value'].unique(),  'coeffs', model_coef[(model_coef['Variable'] == 'TPR_finalized') & (model_coef['Product UPC'] == '22796130723')]['Value'].unique())
  df2.columns = ['%s%s' % (a, '_%s' % b if b else '') for a, b in df2.columns]
  
  return dt_dist,year_dist1

In [ ]:
def _predict(pred_df, model_coef, var_col="model_coefficient_name", coef_col="model_coefficient_value", intercept_name="(Intercept)"):
    """Predict Sales.

    Parameters
    ----------
    pred_df : pd.DataFrame
        Dataframe consisting of IDVs
    model_coef : pd.DataFrame
        Dataframe consisting of model coefficient and its value
    var_col : str
        Column containing model variable
    coef_col : str
        Column containing model variables and their coefficient estimate
    intercept_name : str
        Name of intercept variable

    Returns
    -------
    ndarray
    """
    import numpy as np
    idv_cols = [col for col in model_coef[var_col] if col != intercept_name]
    idv_coef = model_coef.loc[model_coef[var_col].isin(idv_cols), coef_col]
    
    idv_df = pred_df.loc[:, idv_cols]
    

    intercept = model_coef.loc[~model_coef[var_col].isin(idv_cols), coef_col].to_list()[0]
    prediction = idv_df.values.dot(idv_coef.values) + intercept

    #return numpy_exp(prediction)
    #raise Exception(np.exp)
    #f_name = "np.exp(prediction)"
    clean = prediction.astype(np.float64)
    #return eval(f_name)
    return np.exp(clean)


def get_var_contribution_wo_baseline_defined(df, model_coef, wk_sold_price,primary_key,all_df=None, var_col="model_coefficient_name", coef_col="model_coefficient_value", intercept_name="(Intercept)",date_col = "DS", base_var=None):
    """Get variable contribution without baseline defined.

    Parameters
    ----------
    df : pd.DataFrame
        Dataframe consisting of IDVs
    model_coef : pd.DataFrame
        Dataframe consisting of model variables and their coefficient estimate
    wk_sold_price : pd.DataFrame
        Dataframe consisting of weekly sold price
    all_df : pd.DataFrame
        Dataframe consisting of IDVs of all PPGs        
    var_col : str
        Column containing model variable
    coef_col : str
        Column containing model variables' coefficient estimate
    intercept_name : str
        Name of intercept variable
    base_var : list of str
        Base variables

    Returns
    -------
    tuple of pd.DataFrame
    """
    # Predict Sales
    ppg_cols = primary_key
    

    ppg = list(df[primary_key[0]].unique())[0] ##PPG_Item_No replace with Product ID
    model_df = df.drop(columns=ppg_cols).copy() 
    #log_sales = _predict(model_df, model_coef, var_col=var_col, coef_col=coef_col, intercept_name=intercept_name)
    #import numpy as np
    #model_df["Predicted_sales"] = np.exp(_predict(model_df, model_coef, var_col=var_col, coef_col=coef_col, intercept_name=intercept_name))
    model_df["Predicted_sales"] = _predict(model_df, model_coef, var_col=var_col, coef_col=coef_col, intercept_name=intercept_name)

#     print("Coming till step 1")
    # Get base and impact variables
    if base_var is None:
        tpr_features = [i for i in model_coef[var_col] if "PromotedDiscount" in i]
        rp_features = [i for i in model_coef[var_col] if "RegularPrice" in i]
        base_var = ["log_median_baseprice_finalized"] + rp_features + ["ACV", "category_trend", "flag_qtr2", "flag_qtr3", "flag_qtr4", "monthno"]
        base_var = [i for i in base_var if i in model_coef[var_col].to_list()]
        
    base_var = [intercept_name] + base_var
#     print("Working till here??",base_var)
    impact_var = [i for i in model_coef[var_col] if i not in base_var]

    # Get base and impact variables
    model_df[intercept_name] = 1
    tmp_model_coef = model_coef[model_coef[var_col].isin(base_var)]
    tmp_model_df = model_df.copy()
    if all_df is not None: ## All df is none so this won't execute
        if "log_median_baseprice_finalized" in tmp_model_df.columns:
            tmp_model_df = tmp_model_df.merge(all_df.loc[all_df["Product_ID"] == ppg, ["POSWeekStartDate", "avg_price_per_unit"]].drop_duplicates(), how="left", on="POSWeekStartDate")
            tmp_model_df["avg_price_per_unit"] = tmp_model_df["avg_price_per_unit"].astype(np.float64)
            tmp_model_df["log_median_baseprice_finalized"] = np.log(tmp_model_df["avg_price_per_unit"])
            tmp_model_df = tmp_model_df.drop(columns=["avg_price_per_unit"])
        if tmp_model_df.columns.str.contains(".*RegularPrice.*RegularPrice", regex=True).any():
            rp_interaction_cols = [col for col in tmp_model_df.columns if re.search(".*RegularPrice.*RegularPrice", col) is not None]
            for col in rp_interaction_cols:
                col_adj = re.sub(ppg, "", col)
                col_adj = re.sub("_RegularPrice_", "", col_adj)
                col_adj = re.sub("_RegularPrice", "", col_adj)
                tmp_model_df = tmp_model_df.merge(all_df.loc[all_df["Product UPC"] == ppg, ["POSWeekStartDate", "avg_price_per_unit"]], how="left", on="POSWeekStartDate")
                temp = all_df.loc[all_df["Product UPC"] == col_adj, ["POSWeekStartDate", "log_median_baseprice_finalized"]]
                temp = temp.rename(columns={"log_median_baseprice_finalized": "wk_price_log"})
                tmp_model_df = tmp_model_df.merge(temp[["POSWeekStartDate", "wk_price_log"]], how="left", on="POSWeekStartDate")
                tmp_model_df[col] = np.log(tmp_model_df["avg_price_per_unit"]) * tmp_model_df["wk_price_log"]
                tmp_model_df = tmp_model_df.drop(columns=["avg_price_per_unit", "wk_price_log"])
                
    base_val = tmp_model_df[tmp_model_coef[var_col].to_list()].values.dot(tmp_model_coef[coef_col].values)
    
    tmp_model_coef = model_coef[model_coef[var_col].isin(impact_var)]
    impact_val = model_df[tmp_model_coef[var_col].to_list()].values.dot(tmp_model_coef[coef_col].values)
#     print("Working till here 2",base_val)
    model_df["baseline_contribution"] = np.exp(base_val)
    model_df["incremental_contribution"] = model_df["Predicted_sales"] - model_df["baseline_contribution"]
    
    base_val = base_val.astype(np.float64)
    impact_val = impact_val.astype(np.float64)
    # Calculate raw contribution for impact variables
    row_sum =0
    abs_sum = 0
    # print(impact_var)
    for i in impact_var:
        # print("*******************")
        # print(i)
        # print(i+"_contribution_impact")
        # print(model_df.columns)
        
        tmp_impact_val = model_df[i].values * model_coef.loc[model_coef[var_col]==i, coef_col].to_list()[0]
        model_df[i + "_contribution_impact"] = np.exp(base_val + impact_val) - np.exp(base_val + impact_val - tmp_impact_val)
        # print(model_df[i + "_contribution_impact"])
        row_sum = row_sum + model_df[i + "_contribution_impact"]
        abs_sum = abs_sum + np.abs(model_df[i + "_contribution_impact"])

    y_b_s = model_df["incremental_contribution"] - row_sum
    impact_contribution = model_df[[date_col, "Predicted_sales"]].copy()
    for i in  impact_var:
        i_adj = i + "_contribution_impact"
        impact_contribution[i_adj] = model_df[i_adj] + (np.abs(model_df[i_adj])/abs_sum) * y_b_s

    # Calculate raw contribution for base variables
    base_rc = model_coef.loc[model_coef[var_col]==intercept_name, coef_col].to_list()[0]
    impact_contribution[intercept_name + "_contribution_base"] = np.exp(base_rc)
    for i in base_var[1:]:
        t = tmp_model_df[i] * model_coef.loc[model_coef[var_col]==i, coef_col].to_list()[0] + base_rc
        impact_contribution[i + "_contribution_base"] = np.exp(t) - np.exp(base_rc)
        base_rc = t
    impact_contribution = impact_contribution.fillna(0)
    unit_dist_df = impact_contribution.copy()
    
    # Get Dollar Sales
    price_dist_df = unit_dist_df.copy()
    numeric_cols = price_dist_df.select_dtypes(include="number").columns.to_list()
    wk_sold_price = wk_sold_price.astype(np.float64)
    price_dist_df[numeric_cols] = price_dist_df[numeric_cols].mul(wk_sold_price.values, axis=0)
#     print("Working till here 3")
    # Get variable contribution variants
    dt_unit_dist_df, qtr_unit_dist_df, yr_unit_dist_df = get_var_contribution_variants(unit_dist_df, "model_coefficient_name", value_col_name="units")
    dt_price_dist_df, qtr_price_dist_df, yr_price_dist_df = get_var_contribution_variants(price_dist_df, "model_coefficient_name", value_col_name="price")
    overall_dt_dist_df = dt_unit_dist_df.merge(dt_price_dist_df, how="left", on=[date_col, "model_coefficient_name"])
    overall_qtr_dist_df = qtr_unit_dist_df.merge(qtr_price_dist_df, how="left", on=["Quarter", "model_coefficient_name"])
    overall_yr_dist_df = yr_unit_dist_df.merge(yr_price_dist_df, how="left", on=["Year", "model_coefficient_name"])
    
    ppg_df = df[ppg_cols].drop_duplicates().values.tolist()
    overall_dt_dist_df[ppg_cols] = pd.DataFrame(ppg_df, index=overall_dt_dist_df.index)
    overall_qtr_dist_df[ppg_cols] = pd.DataFrame(ppg_df, index=overall_qtr_dist_df.index)
    overall_yr_dist_df[ppg_cols] = pd.DataFrame(ppg_df, index=overall_yr_dist_df.index)

    return overall_dt_dist_df, overall_qtr_dist_df, overall_yr_dist_df


def get_var_contribution_variants(dist_df, var_col_name, value_col_name, date_col = "DS"):
    """Get variable contribution by different variants.

    Parameters
    ----------
    dist_df : pd.DataFrame
        Dataframe consisting of IDVs
    var_col_name : str
        Column name for melted IDV columns
    value_col_name : str
        Column name for IDV values

    Returns
    -------
    tuple of pd.DataFrame
    """
#     print("get_var_contribution_variants function started")
    pct_dist_df = dist_df.copy()
    numeric_cols = pct_dist_df.select_dtypes(include="number").columns.to_list()
#     print("List of vars in numeric_cols",numeric_cols)
    
    pct_dist_df[numeric_cols] = pct_dist_df[numeric_cols].div(pct_dist_df["Predicted_sales"], axis=0)
#     print("working till here4")
    dist_df_1 = pd.merge(dist_df.melt(id_vars=[date_col], var_name=var_col_name, value_name=value_col_name),
                         pct_dist_df.melt(id_vars=[date_col], var_name=var_col_name, value_name="pct_" + value_col_name),
                         how="left", on=[date_col, var_col_name])
    
    # Quarterly Aggegration
    qtr_dist_df = dist_df.copy()
    qtr_dist_df["Quarter"] = qtr_dist_df[date_col].dt.year.astype(str) + "-" + "Q" + qtr_dist_df[date_col].dt.quarter.astype(str)
    qtr_dist_df = qtr_dist_df.drop(columns=[date_col])
    qtr_dist_df = qtr_dist_df.groupby(by=["Quarter"], as_index=False).agg(np.sum)

    pct_qtr_dist_df = qtr_dist_df.copy()
    pct_qtr_dist_df[numeric_cols] = pct_qtr_dist_df[numeric_cols].div(pct_qtr_dist_df["Predicted_sales"], axis=0)
    dist_df_2 = pd.merge(qtr_dist_df.melt(id_vars=["Quarter"], var_name=var_col_name, value_name=value_col_name),
                         pct_qtr_dist_df.melt(id_vars=["Quarter"], var_name=var_col_name, value_name="pct_" + value_col_name),
                         how="left", on=["Quarter", var_col_name])
    
    # Yearly Aggegration 
    yr_dist_df = dist_df.copy()
    yr_dist_df["Year"] = yr_dist_df[date_col].dt.year.astype(str)
    yr_dist_df = yr_dist_df.drop(columns=[date_col])
    yr_dist_df = yr_dist_df.groupby(by=["Year"], as_index=False).agg(np.sum)
    
    pct_yr_dist_df = yr_dist_df.copy()
    pct_yr_dist_df[numeric_cols] = pct_yr_dist_df[numeric_cols].div(pct_yr_dist_df["Predicted_sales"], axis=0)
    dist_df_3 = pd.merge(yr_dist_df.melt(id_vars=["Year"], var_name=var_col_name, value_name=value_col_name),
                         pct_yr_dist_df.melt(id_vars=["Year"], var_name=var_col_name, value_name="pct_" + value_col_name),
                         how="left", on=["Year", var_col_name])
    
    return dist_df_1, dist_df_2, dist_df_3

In [0]:
seasonality_parameter = "REGIONNAME"

#### 3.2 Logging

In [0]:
# logging part
# p_dir = "/dbfs/mnt/solutionsadls2_data/Baseline_Forecasts/processed/"
# os.makedirs(p_dir, exist_ok=True)
log_file = "feature_selection" + " (" +datetime.today().strftime('%Y-%m-%d-%H-%M-%S')+ ").log"

logger = logging.getLogger('custom_log')
logger.setLevel(logging.DEBUG)

# Applying necessary formatter
fh = logging.FileHandler(log_file)
formatter = logging.Formatter("%(asctime)s - %(name)s - %(levelname)s - %(message)s")
fh.setFormatter(formatter)
logger.addHandler(fh)

#### 3.3 Config
Dependent variable, date variable, modeling granularity & other related modeling details are provided in the form of a config file.For LASSO using scipy, we can tune for different values of hyperparameters - alpha & lambda

In [ ]:
import yaml
with open("config_new_updated_v3_weighted.yaml") as file:
    app_config = yaml.safe_load(file)

### 4. Utilities

#### 4.1 Export

#### 4.2 Predict sales

In [0]:
def predict_sales(
    coeffs, data, constant="Intercept", var_col="Parameters", coef_col="Value"
):
    """
    Predecit log lnear model based on model coeff and data.

    Parameters
    ----------
    coeffs: pd.DataFrame()
        model coefficients
    data: pd.DataFrame()
        training or test data
    var_col: str
        Column name in model_coefficients df which contains features
    coef_col: str
        Column name in model_coefficients df which contains feature's values
    intercept_name: str
        fitted constant name

    Returns
    -------
    pd.DataFrame()
        datapredicted volume (y_hat,exp(y_hat)) series along with data
    """

    # predict_column=predict_config["predict_column"]
    predict_column = "pred_vol_log"
    data[predict_column] = 0
    # print("coeffs are", coeffs)
    for i in coeffs[var_col].unique():
        a = coeffs.loc[(coeffs[var_col] == i), coef_col]
        a = a.values
        a = a.astype(np.float64)
        if i == constant:
            # data["pred_vol_log"] = data["pred_vol_log"] + a
           data[predict_column] = data[predict_column] + a

        else:
            # data["pred_vol_log"] = data["pred_vol_log"] + data[i] * a
            data[i] = data[i].astype(np.float64)
            data[predict_column] = data[predict_column] + data[i] * a

    transform_config= "np.exp"
    transformation_col="pred_vol"
    function_name = transform_config
    try:
        transformation_function = eval(function_name)

        data[transformation_col] = transformation_function(
            data[predict_column]
        )
    except (ImportError, AttributeError) as e:
        print(f"Error: Unable to import module or function. Details: {e}")

    return data

#### 4.3 Rsq - MAPE calculation

In [0]:
def rsq_mape(y: pd.Series, y_pred: pd.Series):
  """
  Calculate model performance metrics

  Parameters
  ----------
  y : pd.Series
      Actual dv used in modelling
  y_pred : pd.Series
      Predictions from model

  Returns
  -------
  tuple
      (rsq, wmape)
  """
  SSR = (y - y_pred) ** 2
  SST = (y - np.mean(y)) ** 2
  Rsq2 = 1 - SSR.sum() / SST.sum()
  a1 = np.sum(np.abs(y - y_pred) * y)
  a2 = np.sum(y * y)
  mape = a1 / a2
  return (Rsq2, mape)

#### 4.4 Broadcast helper function
This functions helps to persist the data in all the workers so that we can leverage them in UDF while distributed processing

#### 4.5 Stratified split function

In [0]:
def set_x_df(x_df, test_size, random_state, stratify_cols):
        """
        Get modelling data based on data supplied during class
        initialization.

        Returns
        -------
        x_df: pd.DataFrame()
            Modelling data subset based on idv_default, lasso parameters
            & columns reversed to account for negative dependence
        """
        if len(stratify_cols) > 0:
            stratify_columns = list(set(x_df.columns).intersection(set(stratify_cols)))
            print(x_df.columns)
            print("Stratified Columns:")
            print(stratify_columns)
            stratify_columns1 = stratify_columns.copy()
            for col in stratify_columns1:
                x_df[f"{col}_bin"] = np.where(x_df[col].abs() > 0, 1, 0)
                stratify_columns.remove(col)
                stratify_columns.append(f"{col}_bin")
            final_stratify_cols = stratify_columns.copy()
            final_stratify_cols1 = stratify_columns.copy()
            print(final_stratify_cols1)
            for col in stratify_columns1:
                count = x_df[col].value_counts().reset_index()
                num = 1
                if num in count[col].unique():
                    final_stratify_cols.remove(col)
            print(
                "Stratified Columns after dropping idvs with single value for a group in any class"
            )
            print(final_stratify_cols)
            print(x_df.shape)
            train_x_df, test_x_df = train_test_split(
                x_df,
                test_size=test_size,
                random_state=random_state,
                stratify=x_df[final_stratify_cols],
            )
            x_df.drop(columns=stratify_columns, inplace=True)
            train_x_df.drop(columns=stratify_columns, inplace=True)
            test_x_df.drop(columns=stratify_columns, inplace=True)
        else:
            print("Train-Test split without Stratification")
            train_x_df, test_x_df = train_test_split(
                x_df,
                test_size=test_size,
                random_state=random_state,
            )
        train_df = train_x_df.copy()
        test_df = test_x_df.copy()
        return train_x_df, test_x_df

#### 4.6 Processing Hyperparameter inputs

In [0]:
def frange(start,stop,step= 1):
    l = []
    i = start
    while(i < stop):
        l.append(np.round(i,len(str(step))))
        i = i+step
    return l

def drange(hyperparameters):
    l=[]
    for key in hyperparameters.keys():
        val = hyperparameters[key]
        if 'range' in val:
            val = val.replace('range','frange')
            new_str = 'total_list = '  + val
            _locals = locals()
            exec(new_str,globals(),_locals)
            without_dup = list(set(_locals['total_list']))
            hyperparameters[key] = without_dup
    return hyperparameters

In [0]:
fit_ = drange(app_config["feature_selection"]["lasso_scipy"]["Hyperparameters"])
fit_new = {}
for key in fit_.keys():
    temp = []
    for val in fit_[key]:
        if(type(val) == list):
            val = str(val)
        if((val!='None') and (val!='Null') and (val!=None)):
            temp.append(val)
    if(len(temp)>0):
        fit_new[key] = temp
print(fit_new)        
app_config["feature_selection"]["lasso_scipy"]["Hyperparameters"] = fit_new

{'alpha': [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1], 'lambda': [0.002915, 0.005577, 0.010669, 0.020408, 0.039039, 0.07468, 0.142857, 0.273276, 0.522758, 1.0]}


### 5. Baseline and incremental mapping

In [0]:
baseline_cols = app_config["feature_mapping"]["baseline_cols"] + [f"{seasonality_parameter}_SI_MONTHLY",f'{seasonality_parameter}_SI_QUARTERLY',f"{seasonality_parameter}_SI_WEEKLY"]

increment_cols = app_config["feature_mapping"]["increment_cols"]

increment_other_cols = app_config["feature_mapping"]["increment_other_cols"]

base_incr_mapping = pd.DataFrame({'Parameters':baseline_cols + increment_cols + increment_other_cols,
            'Base_incr_comp':['Base']*len(baseline_cols) + ['Increment_Act']*len(increment_cols) + ['Increment_others']*len(increment_other_cols)})

base_incr_mapping

Parameters Base_incr_comp log_median_baseprice_finalized Base ACV Base internalComp1_MBP Base internalComp2_MBP Base internalComp3_MBP Base internalComp4_MBP Base internalComp5_MBP Base internalComp6_MBP Base internalComp7_MBP Base internalComp8_MBP Base internalComp9_MBP Base internalComp10_MBP Base internalComp11_MBP Base internalComp12_MBP Base internalComp13_MBP Base internalComp14_MBP Base internalComp15_MBP Base trend_year Base trend_quarter Base weighted_mean_GLOBAL_ACV_TDP Base OOS Base internalComp1_TPR Base internalComp2_TPR Base internalComp3_TPR Base internalComp4_TPR Base internalComp5_TPR Base internalComp6_TPR Base internalComp7_TPR Base internalComp8_TPR Base internalComp9_TPR Base internalComp10_TPR Base internalComp11_TPR Base internalComp12_TPR Base internalComp13_TPR Base internalComp14_TPR Base internalComp15_TPR Base TPR_finalized_lag1 Base TPR_finalized_lag2 Base TPR_finalized_lag3 Base TPR_finalized_lag4 Base CATEGORY_CLUSTER_si_weekly Base CATEGORY_CLUSTER_si_quarterly Base CATEGORY_CLUSTER_si_monthly Base TPR_finalized Increment_Act display_flag_ratio Increment_Act feat_flag_ratio Increment_Act TPR_finalized_lag1 Increment_others TPR_finalized_lag2 Increment_others TPR_finalized_lag3 Increment_others TPR_finalized_lag4 Increment_others canada_day Increment_others christmas_day Increment_others civic_holiday Increment_others easter_monday Increment_others good_friday Increment_others labor_day Increment_others major Increment_others minor Increment_others national_day_for_truth_and_reconciliation Increment_others new_year_s_day Increment_others remembrance_day Increment_others thanksgiving_day Increment_others victoria_day Increment_others Pre_Christmas_Promo_Flag Increment_others

### 6. Contribution Calculation 

In [0]:
def run_prediction_and_contribution_analysis(
    best_lasso_models,
    model_data,
    base_incr_mapping,
    predict_sales_func,
    contribution_cal_base_variable_func,
    idv_column='Parameters',
    intercept_name='Intercept',
    date_column='DS',
    coef_col='Value',
    avg_price_column='ASP',
    primary_key=["F_CODE"],
    base_col_substr_order=None
):
    if base_col_substr_order is None:
        # base_col_substr_order = [
        #    "log_median_baseprice_finalized",
        #     'internalComp1_MBP','internalComp2_MBP','internalComp3_MBP','internalComp4_MBP','internalComp5_MBP','internalComp6_MBP','internalComp7_MBP','internalComp8_MBP','internalComp9_MBP','internalComp10_MBP','internalComp11_MBP','internalComp12_MBP','internalComp13_MBP','internalComp14_MBP','internalComp15_MBP',
        #     'internalComp1_TPR','internalComp2_TPR','internalComp3_TPR','internalComp4_TPR','internalComp5_TPR','internalComp6_TPR','internalComp7_TPR','internalComp8_TPR','internalComp9_TPR','internalComp10_TPR',"internalComp11_TPR","internalComp12_TPR","internalComp13_TPR","internalComp14_TPR","internalComp15_TPR",
        #     'trend_year','trend_quarter',f"{seasonality_parameter}_si_weekly",f'{seasonality_parameter}_si_quarterly',
        #     f"{seasonality_parameter}_si_monthly", "ACV",'OOS',
        # ]
        base_col_substr_order = [
            'TREND_YEAR','TREND_MONTH','TREND_QUARTER',f"{seasonality_parameter}_SI_WEEKLY",f'{seasonality_parameter}_SI_QUARTERLY',
            f"{seasonality_parameter}_SI_MONTHLY","CPI","UNEMPLOYMENT_RATE","PRIMED_LEADS"
        ]

    simulated_data_w_predictions_list = []
    contribution_data_list = []

    for pf in best_lasso_models['Iteration_ID'].unique().tolist():
        print(f"Processing: {pf}, F_CODE: {pf.split('_')[0]}")

        coeff_pf = best_lasso_models[best_lasso_models['Iteration_ID'] == pf].copy()
        coeff_pf = coeff_pf.rename(columns={'IDV': idv_column})
        df = model_data.copy()

        # Predict sales
        df = predict_sales_func(coeff_pf, df)
        # df.display()

        # Merge mapping
        coeff_pf = pd.merge(coeff_pf, base_incr_mapping, on=idv_column, how="left")
        
        # Contribution calculation
        # coeff_pf.display()
        # raise Exception("columns", df.columns)
        dt_dist_base_var, year_dist_base_var = contribution_cal_base_variable_func(
            coeff_pf.copy(), df.copy(), base_col_substr_order, idv_column,
            intercept_name, date_column, coef_col, avg_price_column, primary_key
        )
        
        contribution_df = dt_dist_base_var.copy()
        contribution_df['Iteration_ID'] = pf
        # contribution_df.display()
        # Store results
        # simulated_data_w_predictions_list.append(df)
        contribution_data_list.append(contribution_df)
    contribution_data = pd.concat(contribution_data_list)
    contribution_data = contribution_data.reset_index(drop = True)

    return contribution_data


In [0]:
logger.info("Config file read")

# For exporting the config file
temp_config = app_config.copy()

INFO:custom_log:Config file read


### 8. Broadcasting the required variables
Variables suffixed with "_conf" are taken from the config file

In [0]:
modeling_granularity_conf = app_config["general_inputs"]["modeling_granularity"]
# print(modeling_granularity_conf)

# Rename Start date and DV config
dv_config = app_config["general_inputs"]["dependent_variable"]
ds_config = app_config["general_inputs"]["date_var"]

# pos and neg corr broadcast
corr_config_broadcast = app_config['feature_selection']['exogenous_variables']

hyperparameters_conf = dict(app_config["feature_selection"]["lasso_scipy"]["Hyperparameters"])
broadcast_hyper_parameters = hyperparameters_conf
broadcast_metric = app_config["feature_selection"]["lasso_scipy"]["metric"]

broadcast_granularity = modeling_granularity_conf
broadcast_req_info = app_config['feature_selection']['lasso_scipy']
broadcast_tracking = app_config['tracking']
logger.info("Broadcasted the required variables")

INFO:custom_log:Broadcasted the required variables


In [0]:
hyperparameters_conf

{'alpha': [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1],
 'lambda': [0.002915,
  0.005577,
  0.010669,
  0.020408,
  0.039039,
  0.07468,
  0.142857,
  0.273276,
  0.522758,
  1.0]}

### 9. Creating the hyperparameter grid

In [0]:
# Creating a hyperparameter grid using the set of provided hyperparameters in the config file
def create_hyperparam_space(hp_space: dict) -> pd.DataFrame:
    """Function to create a hyperparameter grid using the set of provided hyperparameters in the config file to be used for Hyperparameter tuning

    Parameters
    ----------
    hp_space : dict
        The set of provided hyperparameters in the config file

    Returns
    -------
    pd.DataFrame
        Returns a hyperparameter grid created from the set of provided hyperparameters
    """    
    df_list = list()
    for x in hp_space:
      df_list.append(pd.DataFrame({x:hp_space[x]}))

    space=df_list[0]

    for x in df_list[1:]:
        space = space.merge(x,how="cross")

    return space

### 10. Base class for doing LASSO

In [0]:
class ElasticNetRegression:
    """
    ElasticNetRegression class for TPO models.
    It is assumed that log-log model is used.

    .. math::
        \frac{\sum_{i=1}^m(y_{i} - x{'}_{i}\hat{\beta})^2}{2m} + \lambda\frac{1-\alpha}{2}\sum_{j=1}^n\hat{\beta}_j^{2} + \lambda\alpha\left | \hat{\beta}_j \right |
    """

    def __init__(self):
        pass

    def elastic_net_cost_function(
        self,
        coef: list,
        X: pd.DataFrame,
        y: pd.Series,
        penalty: list,
        alpha: float,
        lambda_: float,
        intercept: bool,
    ):
        """
        Cost function to be minimized while fitting the model

        Parameters
        ----------
        coef : list
            List of coefficients including intercept
        X : pd.DataFrame
            Dataframe containing idvs
        y : pd.Series
            Series containing dependent variable
        penalty : list
            Penalty factors
        alpha : float, range between [0,1]
            determines extent of l1 & l2 regularization
        lambda_ : float
            determines severity of penalty
        intercept : bool
            determines whether intercept should be fitted to the model

        Returns
        -------
        float
            cost w.r.t given iteration
        """
        m = len(y)
        if intercept:
            intercept_coef = coef[0]
            coef_ = coef[1:]
        else:
            intercept_coef = 0
            coef_ = coef

        y_pred = intercept_coef + X.dot(coef_)
        residuals = y - y_pred
        mse = 0.5 * np.mean(residuals**2)
        
        penalty = np.array(penalty)
        l2_norm = np.sum(penalty * (coef_**2))
        l1_norm = np.sum(penalty * np.abs(coef_))
        penalty_term = 0.5 * (1 - alpha) * l2_norm + alpha * l1_norm

        return mse + lambda_ * penalty_term

    def create_bound_dict(
        self, idvs: list, pos_impact_idvs: list, neg_impact_idvs: list
    ):
        """
        Create bound dict of the form {idv: (lb, ub)}

        Parameters
        ----------
        idvs : list
            List of IDVs to be used in modelling
        pos_impact_idvs : list
            List of IDVs whose coefficient should be positive
        neg_impact_idvs : list
            List of IDVs whose coefficient should be negative

        Returns
        -------
        dict
            Dictionary containing upper and lower bounds for input variables
        """
        param_bound_dict = {}
        for idv in idvs:
            if idv in pos_impact_idvs:
                param_bound_dict.update({idv: (0, np.inf)})
            elif idv in neg_impact_idvs:
                param_bound_dict.update({idv: (-np.inf, 0)})
            else:
                param_bound_dict.update({idv: (-np.inf, np.inf)})
        return param_bound_dict

    def create_penalty_list(self, idvs: list, zero_penalty_cols: list, inc_penality_cols, inc_penality):
        """
        Creates list of penalty factors to be applied during regularization.
        By default a penalty = 1 is applied on all variables.
        Variables for which penalty need not be applied can be passed as forcefit_cols.
        Internally, the list of penalty factors is scaled such that the sum matches the
        number of IDVs.

        Parameters
        ----------
        idvs : list
            List of IDVs to be used in modelling
        zero_penalty_cols : list
            List of variables to be excluded from applying penalty

        Returns
        -------
        list
            List containing penalty factor to be applied on model IDVs.
        """
        penalty = []
        if len(inc_penality_cols) != 0:
            penalty = [0 if idv in zero_penalty_cols else inc_penality if idv in inc_penality_cols else 1 for idv in idvs]

        else:
            penalty = [0 if idv in zero_penalty_cols else 1 for idv in idvs]
        penalty_sum = np.sum(penalty)
        n = len(idvs)
        penalty = [i * n / penalty_sum for i in penalty]
        # raise Exception(penalty)
        return penalty


    def predict(self, coeffs: pd.DataFrame, data: pd.DataFrame):
        """
        Predict method for elastic net model. The prediction is returned in log scale.

        Parameters
        ----------
        coeffs : pd.DataFrame
            Contains coefficients for IDVs
        data : pd.DataFrame
            Data on which prediction needs to be done.

        Returns
        -------
        pd.Series
            Contains predictions in log scale
        """
        y_pred = pd.Series([0] * data.shape[0])
        for i in coeffs["Parameters"].unique():
            a = coeffs.loc[(coeffs["Parameters"] == i), "Value"]
            a = a.values
            if i == "Intercept":
                y_pred = y_pred + a
            else:
                y_pred = y_pred + data[i] * a
        return y_pred

    def rsq_mape(self, y: pd.Series, y_pred: pd.Series):
        """
        Calculate model performance metrics

        Parameters
        ----------
        y : pd.Series
            Actual dv used in modelling
        y_pred : pd.Series
            Predictions from model

        Returns
        -------
        tuple
            (rsq, wmape)
        """
        SSR = (y - y_pred) ** 2
        SST = (y - np.mean(y)) ** 2
        Rsq2 = 1 - SSR.sum() / SST.sum()
        a1 = np.sum(np.abs(y - y_pred) * y)
        a2 = np.sum(y * y)
        mape = a1 / a2
        return (Rsq2, mape)

    def fit(
        self,
        data: pd.DataFrame,
        dv: str,
        idvs: list,
        zero_penalty_cols: list = [],
        pos_impact_idvs: list = [],
        neg_impact_idvs: list = [],
        user_bound_dict: dict = {},
        alpha: float = 1,
        lambda_: float = 1,
        intercept: bool = True,
        model_eval_level: list = ["week_start_date"],
        coeff_tol: float = 1e-05,
        inc_penality_cols = [], 
        inc_penality = [],
        test_size: float = 0.2, 
        random_state: int = 42 
        
    ):
        """
        Fit method for elastic net regression.

        Parameters
        ----------
        data : pd.DataFrame
            model data
        dv : str
            dependent variable
        idvs : list
            list of idvs to be used for modelling
        zero_penalty_cols : list, optional
            list of variables to be excluded from penalty, by default []
        pos_impact_idvs : list, optional
            list of IDVs whose coefficient should be positive, by default []
        neg_impact_idvs : list, optional
            list of IDVs whose coefficient should be positive, by default []
        user_bound_dict : dict, optional
            user defined bounds for regression, by default {}
            format of dict should be {idv: (lb, ub)}
        alpha : float, optional
            determines mix between l1 and l2 regularization, by default 1
            alpha = 1 implies complete l2 regularization &
            alpha = 0 implies complete l1 regularization
        lambda_ : float, optional
            penalty coefficient, by default 1
        intercept : bool, optional
            determines whether intercept should be fitted to the model, by default True
        model_eval_level : list, optional
            to be added if performance metrics need to be aggregated at a given
            granularity, by default ["week_start_date"]
        coeff_tol: float, optional
            threshold for absolute value of coefficients, by default 1e-05 
            Variables whose coefficients are less than mentioned value are dropped from final model.
        test_size : float, optional
            Proportion of data to use as the test set, by default 0.2
        random_state : int, optional
            Random seed for reproducibility, by default 42
        
        Returns
        -------
        pd.DataFrame
            coefficient dataframe with performance metrics (rsq2, wmape)
        """
        # Splitting the data into training and testing sets
        # train_data, test_data = train_test_split(data, test_size=test_size, random_state=random_state)
        

        # Use training data to fit the model
        X = data[idvs]
        y = data[dv]
        n = X.shape[1]
        
        # Rest of the existing fitting logic
        penalty = self.create_penalty_list(idvs, zero_penalty_cols, inc_penality_cols = inc_penality_cols, 
        inc_penality = inc_penality)
        param_bound_dict = self.create_bound_dict(
            idvs, pos_impact_idvs, neg_impact_idvs
        )
        if len(user_bound_dict) != 0:
            param_bound_dict.update(user_bound_dict)
        param_bounds = [param_bound_dict[idv] for idv in idvs]

        if intercept:
            x0 = np.zeros(n + 1)
            bounds = [(-np.inf, np.inf)] + param_bounds
        else:
            x0 = np.zeros(n)
            bounds = param_bounds

        opt_result = minimize(
            functools.partial(
                self.elastic_net_cost_function,
                X=X,
                y=y,
                penalty=penalty,
                alpha=alpha,
                lambda_=lambda_,
                intercept=intercept,
            ),
            x0=x0,  # Initial guess for coefficients
            bounds=bounds,
        )

        lasso_coeff = pd.DataFrame()
        if intercept:
            lasso_coeff["Parameters"] = ["Intercept"] + idvs
        else:
            lasso_coeff["Parameters"] = idvs

        lasso_coeff["Value"] = opt_result.x

        lasso_coeff['abs'] = np.abs(lasso_coeff["Value"])
        lasso_coeff = lasso_coeff[lasso_coeff['abs'] > coeff_tol].reset_index(drop=True)
        lasso_coeff = lasso_coeff.drop(['abs'], axis=1)
        
        # raise Exception("fit method coeffs",lasso_coeff)
        # Making predictions on the training set
        y_pred = self.predict(coeffs=lasso_coeff, data=X)


        if len(model_eval_level) != 0:
            actual_vs_pred = data[model_eval_level].copy()
            actual_vs_pred["Actuals"] = np.exp(y.values) - 1
            actual_vs_pred["Pred"] = np.exp(y_pred.values) - 1
            actual_vs_pred = (
                actual_vs_pred.groupby(model_eval_level).sum().reset_index()
            )
        else:
            actual_vs_pred = pd.DataFrame()
            actual_vs_pred["Actuals"] = np.exp(y.values) - 1
            actual_vs_pred["Pred"] = np.exp(y_pred.values) - 1

        rsq, wmape = self.rsq_mape(
            y=actual_vs_pred["Actuals"], y_pred=actual_vs_pred["Pred"]
        )
        # to handle erroneous results epsilon is set to 1.
        epsilon = 1
        
        mape = np.mean(np.abs(actual_vs_pred["Actuals"] - actual_vs_pred["Pred"]) / np.maximum(np.abs(actual_vs_pred["Actuals"]), epsilon))*100
        bias= np.mean((actual_vs_pred["Actuals"] - actual_vs_pred["Pred"]))  
        tracking_signal = np.sum((actual_vs_pred["Actuals"] - actual_vs_pred["Pred"])) / np.mean(np.abs(actual_vs_pred["Actuals"] - actual_vs_pred["Pred"]))
        mae = mean_absolute_error(actual_vs_pred["Actuals"], actual_vs_pred["Pred"])
        rmse=np.sqrt(mean_squared_error(actual_vs_pred["Actuals"], actual_vs_pred["Pred"]))
        smape = np.mean(np.abs(actual_vs_pred["Actuals"] - actual_vs_pred["Pred"]) / np.maximum(np.abs(actual_vs_pred["Actuals"]) + np.abs(actual_vs_pred["Pred"]), epsilon))*100

        lasso_coeff["rsq"] = rsq
        lasso_coeff["wmape"] = wmape
        lasso_coeff["mape"] = mape
        lasso_coeff["bias"] = bias
        lasso_coeff["tracking_signal"] = tracking_signal
        lasso_coeff["mae"] = mae
        lasso_coeff["rmse"] = rmse
        lasso_coeff["smape"] = smape

        n_lasso = lasso_coeff.shape[0]
        lasso_coeff["alpha"] = [alpha] * n_lasso
        lasso_coeff["lambda_"] = [lambda_] * n_lasso
        lasso_coeff["log_lambda"] = np.log10(lasso_coeff["lambda_"])
        return lasso_coeff

In [ ]:
from snowflake.snowpark.types import StructType, StructField, IntegerType, StringType, DateType, FloatType

In [ ]:
def get_perf_metrics(y, yhat):
    
    epsilon = 1
    
    mape = np.mean(np.abs(y - yhat) / np.maximum(np.abs(y), epsilon))*100
    bias= np.mean((y - yhat))  
    tracking_signal = np.sum((y - yhat)) / np.mean(np.abs(y - yhat))
    mae = mean_absolute_error(y, yhat)
    rmse=np.sqrt(mean_squared_error(y, yhat))
    smape = np.mean(np.abs(y - yhat) / np.maximum(np.abs(y) + np.abs(yhat), epsilon))*100

    return {"mape":mape, "bias":bias, "tracking_signal":tracking_signal, "mae":mae, "rmse":rmse,"smape":smape}

In [0]:
def create_dynamic_schema(aggregated: bool = False) -> StructType:
    """Function to create the schema of the dataset to be used in Pandas UDFs

    Parameters
    ----------
    aggregated : bool, optional
        if False, will be creating the schema for the backtesting output else if True, will be creating the schema for getting best hyperparameters

    Returns
    -------
    StructType
        Returns the created dynamic schema of the columns of all the required variables
    """
    result_schema = []

    if aggregated == False:
      result_schema = broadcast_train_test_rsq_mape_check_schema = [
        StructField(modeling_granularity_conf[0],StringType()),
        StructField(ds_config,StringType()),
        StructField("Iteration_ID", StringType()),
        StructField("contributions",StringType()),
        StructField("model_coefficients",StringType()),
        StructField("status",StringType()),
      ]

    else:
      result_schema = broadcast_train_test_rsq_mape_check_schema = [
        StructField(modeling_granularity_conf[0],StringType()),
        StructField(ds_config,StringType()),
        StructField("Iteration_ID", StringType()),
        StructField("contributions",StringType()),
        StructField("model_coefficients",StringType()),
        StructField("status",StringType()),
    ]
    
    return StructType(result_schema)

### 11. UDF for Feature Selection

In [0]:
def change_si_zero_penalty(df):
    seasonality_corr = df[[f'{seasonality_parameter}_si_weekly','POSQuantity']].corr()[f'{seasonality_parameter}_si_weekly']['POSQuantity']
    return seasonality_corr

In [ ]:
from sklearn.preprocessing import StandardScaler, MinMaxScaler

In [ ]:
#@pandas_udf(imports=["@contribution_calc_updated/contribution_calc_updated.py"])
def get_forecast_UDF2(df_data: pd.DataFrame)-> pd.DataFrame:
    """Function to perform model building using the entire data to get the significant features utilizing the broadcasted details from the config file

    Parameters
    ----------
    df_data : pd.DataFrame
        The dataset containing values for all the required variables

    Returns
    -------
    pd.DataFrame
        Returns a dataframe with the granularity x variable
    """
    print('in UDF func')
    try:
        #from contribution_calc_updated import run_prediction_and_contribution_analysis
        #df_data = df_data.rename({"DS":'ds',"Y":"y"})
        df_data_og = df_data.copy()
        #random.seed(123)
        import numpy as np
        np.random.seed(42)
        # try:
        #     train,test = set_x_df(df_data, 0.2, 42, ["TPR_finalized"])
        # except:
            # print(list(xi.columns))
        df_data = df_data.sort_values(by=['DS'],ascending=True).reset_index(drop = True)
        df_data['Y'] = df_data['Y'].clip(lower=df_data['Y'].quantile(0.01),
                                    upper=df_data['Y'].quantile(0.99))
        
        # X_train, X_test, y_train, y_test = train_test_split(df_data.drop(['Y'], axis = 1), df_data['Y'], test_size=0.2, random_state=42, shuffle=False)
        df_data["CPI"] = df_data["CPI"].replace(0, np.nan)
        df_data["UNEMPLOYMENT_RATE"] = df_data["UNEMPLOYMENT_RATE"].replace(0, np.nan)
        df_data[["CPI","UNEMPLOYMENT_RATE"]] = df_data[["CPI","UNEMPLOYMENT_RATE"]].ffill()
        # train = X_train.copy()
        # train['y'] = y_train
        # test = X_test.copy()
        # test['y'] = y_test
        train_start_date = pd.to_datetime("2022-07-04")
        test_start_date = pd.to_datetime("2025-08-04")
        test_end_date = pd.to_datetime("2025-11-03")
        train = df_data[(df_data['DS'] >= train_start_date) & (df_data['DS'] < test_start_date)]
        train['y'] = train["Y"]
        test  = df_data[(df_data['DS'] >= test_start_date) & (df_data['DS'] <= test_end_date)]
        test['y'] = test["Y"]
        test[["CPI","UNEMPLOYMENT_RATE"]] = test[["CPI","UNEMPLOYMENT_RATE"]].ffill()
        print(test[["CPI","UNEMPLOYMENT_RATE"]])
        corr_var = corr_config_broadcast
        
        regressors = list(set(corr_var["positive_corr"] + corr_var["negative_corr"]+corr_var['uncertain_corr']))
        #Scaling
        ##1. Select only numeric columns
        #num_cols = train.select_dtypes(include=['int64', 'float64']).columns
        
        #2. Initialize scaler
        scaler = MinMaxScaler()
        
        # 3. Fit and transform numeric columns
        train[regressors] = scaler.fit_transform(train[regressors])
        test[regressors] = scaler.transform(test[regressors])
        print(test[["CPI","UNEMPLOYMENT_RATE"]])
        df_data_og = pd.concat([train, test], axis = 0)
        
        df_data = train.copy()
        df_data = df_data.sort_values(by=['DS'],ascending=True).reset_index(drop = True)
        # broadcast_granularity
        broadcast_gran = broadcast_granularity
        
        req_info = broadcast_req_info
        # Appending regressors based on the sign of correlation
        
        regressors = list(set(corr_var["positive_corr"] + corr_var["negative_corr"]+corr_var['uncertain_corr']))
        regressors = [i for i in regressors if i in list(df_data.columns)]
        
        temp_list1 = []
        # Removing regressors based on the correlation
        if(corr_var["consider_correlation"]):   
            for x in corr_var["positive_corr"]:
                if(df_data[['y',x]].corr().iloc[0][1]<0):
                    temp_list1.append(x)
            for x in corr_var["negative_corr"]:
                if (x not in temp_list1):
                    if(df_data[['Y',x]].corr().iloc[0][1]>0):
                        temp_list1.append(x)   
            regressors = list(set(regressors) - set(temp_list1))
        
        print("check 1")
        # Checking for variance in the regressor
        temp_list2 = []
        if len(regressors)>0:
            for ex_var in regressors: 
                df_data[ex_var] = (
                    df_data[ex_var]
                    .apply(lambda v: float(v) if v is not None else np.nan)  # convert Decimal to float
                    .astype("float64")
                )
                mean = df_data[ex_var].mean()
                std = df_data[ex_var].std()
                if mean == 0:
                    if std <= 0.001:
                        temp_list2.append(ex_var)
                else:
                    if np.abs(std/mean) <= 0.01:
                        temp_list2.append(ex_var)
        print("check 1")
        if(len(temp_list2)>0):
            for var in temp_list2:
                regressors.remove(var)
        reg_len = len(regressors)
        
        ### IDVs and DV
        X=df_data[regressors].to_numpy()
        y=df_data[['y']].astype(float).to_numpy()
        if(req_info['consider_limits']):
            pos_impact_idvs = corr_var["positive_corr"]
            neg_impact_idvs = corr_var["negative_corr"]
        else:
            pos_impact_idvs = []
            neg_impact_idvs = []
        zero_penalty_cols = req_info['zero_penalty_vars']
        zero_penalty_cols = [var for var in zero_penalty_cols if var in regressors]
        print(zero_penalty_cols)
        # Should be of the form {idv: (lb, ub)}
        #user_bound_dict = {"tpr_discount_byppg": (0, 0.04),
        #"wk_sold_median_base_price_byppg_log": (-2,-0.5),}
        user_bound_dict = {"TOTAL_SPENDS_OVERALL": (0, 0.3),
                           "TOTAL_SPENDS_OVERALL_LAG1": (0, 0.3),
                           "TOTAL_SPENDS_OVERALL_LAG2": (0, 0.3),
                          "PRIMED_LEADS": (0, 0.3),
                          # "REGIONNAME_SI_MONTHLY": (0, 0.1),
                          # "REGIONNAME_SI_QUARTERLY": (0, 0.1),
                           "REGIONNAME_SI_WEEKLY": (0, 0.3)
                          }

        hp_config = broadcast_hyper_parameters
        reg_dict = {"alpha":0, "lambda":0}
        for x in hp_config:
            reg_dict[x] = df_data[x.upper()].iloc[0]

        regression = ElasticNetRegression()
        print(df_data.shape)
        def lasso_and_cont(inc_penality_cols, inc_penality,zero_penalty_cols, test):

            model_coefficients_final = regression.fit(
                data=df_data,
                dv="y",
                idvs=regressors,
                zero_penalty_cols=zero_penalty_cols,
                pos_impact_idvs=pos_impact_idvs,
                neg_impact_idvs=neg_impact_idvs,
                user_bound_dict=user_bound_dict,
                alpha=reg_dict["alpha"],
                lambda_=reg_dict["lambda"],
                intercept=True,
                model_eval_level=["DS"],
                coeff_tol=1e-05,
                inc_penality_cols = inc_penality_cols, 
                inc_penality = inc_penality
            )
            #model_coefficients_final = pd.DataFrame()
            for var in broadcast_gran:
                model_coefficients_final[var] = df_data[var].iloc[0]
                model_coefficients_final[var] = model_coefficients_final[var].astype(str)
            model_coefficients_final = model_coefficients_final[broadcast_gran + ['Parameters','Value','mape','wmape','bias','tracking_signal','mae','rmse','smape','rsq']]
            model_coefficients_final['status'] = 'success'
            model_coefficients_final["alpha"] = reg_dict["alpha"]
            model_coefficients_final["lambda"] = reg_dict["lambda"]
            model_coefficients_final.rename(columns = {'rsq':'train_rsq','wmape':'train_wampe'})

            # Score test data
            # X_test = test[regressors]
            test =  predict_sales(coeffs=model_coefficients_final[['Parameters','Value']].drop_duplicates(), data = test)
            y_test = test["y"]
            
            # raise Exception("data shape",X_test.shape[0],"y_test_predv",y_test_predv)
            test["Actuals"] = np.exp(y_test.values) - 1
            test["Pred"] = test['pred_vol']
            print(test[["DS","Actuals","Pred","y"]])
            test_rsq, test_wmape = rsq_mape(
                y=test["Actuals"], y_pred=test["Pred"]
            )

            model_coefficients_final['test_wmape'] = test_wmape
            model_coefficients_final['test_rsq'] = test_rsq
            metrics_dict = get_perf_metrics(test["Actuals"], test["Pred"])
            model_coefficients_final['test_mape'] = metrics_dict["mape"]
            model_coefficients_final['test_bias'] = metrics_dict["bias"]
            model_coefficients_final['test_tracking_signal'] = metrics_dict["tracking_signal"]
            model_coefficients_final['test_rmse'] = metrics_dict["rmse"]
            model_coefficients_final['test_mae'] = metrics_dict["mae"]
            model_coefficients_final['test_smape'] = metrics_dict["smape"]

            model_coefficients_final.rename(columns = {"Value":"Coeff"}, inplace = True)
            model_coefficients_final['Iteration_ID'] = model_coefficients_final[['F_CODE','alpha','lambda']].astype(str).apply(lambda x: '_'.join(x),axis=1)
            model_coefficients_final.rename(columns = {'Coeff':'Value'}, inplace = True)
            total_no_of_idvs = model_coefficients_final['Parameters'].nunique()
            df_data_og[ds_config] = df_data_og['DS']
            #if total_no_of_idvs <= 13:
            if total_no_of_idvs <= 60:
                if 'Intercept' in model_coefficients_final['Parameters'].unique():
                    if model_coefficients_final[model_coefficients_final['Parameters'] == 'Intercept']['Value'].values[0] > 0:
                        contrib_data = run_prediction_and_contribution_analysis(
                            best_lasso_models=model_coefficients_final,
                            model_data =df_data_og,
                            base_incr_mapping=base_incr_mapping,
                            predict_sales_func=predict_sales,
                            contribution_cal_base_variable_func=contribution_cal_base_variable,
                        )
                else:
                    contrib_data = pd.DataFrame()
            else:
                contrib_data = pd.DataFrame()

            return model_coefficients_final, contrib_data
            #return model_coefficients_final
        comp_cols = [i for i in df_data_og.columns if 'internal' in i]
        model_coefficients_final,contrib_data = lasso_and_cont(inc_penality_cols = comp_cols, inc_penality = 4, zero_penalty_cols = zero_penalty_cols, test = test)
        

        # comp_tpr_cont_cols = [i for i in contrib_data.columns if '_TPR_contribution_impact' in i and 'internal' in i]
        # if len(comp_tpr_cont_cols) > 0:
        #     comp_tpr_cont_tot = contrib_data[comp_tpr_cont_cols].sum(axis=1).sum()
        #     try:
        #         total_units = contrib_data['Predicted_sales'].sum()
        #     except:
        #         raise Exception('contrib columns are:',contrib_data.columns)
        #     comp_cont_perc = np.abs(comp_tpr_cont_tot/total_units)
        #     if comp_cont_perc > 0.1:
        #         model_coefficients_final, contrib_data = lasso_and_cont(inc_penality_cols = comp_cols, inc_penality = 6,zero_penalty_cols = zero_penalty_cols, test = test)

        # if f'{seasonality_parameter}_si_weekly_contribution_base' in contrib_data.columns:
        #     si_weekly_cont_tot = contrib_data[[f'{seasonality_parameter}_si_weekly_contribution_base']].sum(axis=1).sum()
        #     total_units = contrib_data['Predicted_sales'].sum()
        #     si_cont_perc = si_weekly_cont_tot / total_units
        #     if si_cont_perc > 0.3:
                
        #         zero_penalty_cols = [i for i in zero_penalty_cols if i != f'{seasonality_parameter}_si_weekly']
        #         zero_penalty_cols = zero_penalty_cols + [f'{seasonality_parameter}_si_monthly']
        #         model_coefficients_final, contrib_data = lasso_and_cont(inc_penality_cols = comp_cols, inc_penality = 4, zero_penalty_cols = zero_penalty_cols,test = test)

        
        report_df = df_data_og[[modeling_granularity_conf[0],ds_config]].drop_duplicates()
        report_df['Iteration_ID'] = model_coefficients_final[['F_CODE','alpha','lambda']].astype(str).apply(lambda x: '_'.join(x),axis=1).values[0]
        if contrib_data.shape[0] > 0:
            contrib_data["DS"] = contrib_data["DS"].dt.date
            contrib_data["DS"] = contrib_data["DS"].astype(str)
            report_df['contributions'] = contrib_data.to_dict(orient='records')
        else:
            report_df['contributions'] = None
        report_df['contributions'] = report_df['contributions'].astype(str)
        #report_df['contributions'] = ""
        report_df['model_coefficients'] = str(model_coefficients_final.to_dict())
        report_df['model_coefficients'] = report_df['model_coefficients'].astype(str)
        report_df[ds_config] = report_df[ds_config].astype(str)
        report_df['status'] = 'success'
        print("MAPE --->",model_coefficients_final.to_dict()["mape"][0])
        print("WMAPE --->",model_coefficients_final.to_dict()["wmape"][0])
        
        return report_df
      
    except Exception as e:
        print(traceback.format_exc())
        report_df = pd.DataFrame(columns = broadcast_granularity + ['Iteration_ID',ds_config,'contributions','model_coefficients'],index = range(1))
        report_df[broadcast_granularity] = df_data[broadcast_granularity].head(1).reset_index(drop = True)
        for x in broadcast_granularity:
            report_df[x] = report_df[x].astype(str)
        report_df['status'] = str(traceback.format_exc())  
        return report_df


#### 11.1 Loading the latest `modeling_input` file

In [ ]:
# Read the latest harmonized data
#df = session.table("MY_TEMP_ADS_TABLE_V5")
#df = session.table("FEATURE_ENGINEERING_OUTPUT")
df = session.table("MISSING_VALUE_TREATMENT_NON_PROMO_SEASONALITY")
promo_df = session.table("PROMO_DATA_WEIGHTED")

In [ ]:
df.count()

In [ ]:
df

In [ ]:
df_new = df.join(promo_df, on = ["F_CODE","START_OF_WEEK"], how = "left")

In [ ]:
df_new

In [ ]:
cols_to_avg = ["FMF","NMF","FM","KICK_START","FOUNDER","RR","WINBACK_CORP","SUMMER","AOJO","NEWVEMBER","FAO","OTHER","AOAO","DSO","PROMO"]
from snowflake.snowpark.functions import col, lit, when
numerator = None
for c in cols_to_avg:
    expr = when((col(c).is_not_null()) & (col(c) != 0), col(c)).otherwise(lit(0))
    numerator = expr if numerator is None else numerator + expr

denominator = None
for c in cols_to_avg:
    expr = when((col(c).is_not_null()) & (col(c) != 0), lit(1)).otherwise(lit(0))
    denominator = expr if denominator is None else denominator + expr

df = df.with_column(
"PROMO_INTENSITY",
F.when(denominator == 0, 0)
 .otherwise(numerator / denominator)
)


In [ ]:
df = df.with_column(
    "PROMO_INTENSITY_MAX",
    F.greatest(*[F.col(c) for c in cols_to_avg])
)

In [ ]:
df

In [ ]:
# ",".join([f"'{i}'" for i in df.columns if "DAY" in i])

In [ ]:
df = df_new.fillna(0)
df = df.with_column_renamed(dv_config,"y")
df = df.with_column_renamed(ds_config,"ds")

logger.info("Data loaded")

# 2. Create the hyperparameter space
hpspace = create_hyperparam_space(hyperparameters_conf)
logger.info("Created hyperparameter grid")

# 3. Create the result schema for the UDF
result_schema = create_dynamic_schema()
logger.info("Created schema")

In [ ]:
df

In [ ]:
df_hp = session.create_dataframe(hpspace)

In [ ]:
df_hp.columns

In [ ]:
df_hp = df_hp.with_column_renamed('"alpha"',"ALPHA")
df_hp = df_hp.with_column_renamed('"lambda"',"LAMBDA")

In [ ]:
df_hp

In [0]:
f_df = df.cross_join(df_hp)
gbcp = list(modeling_granularity_conf) + list(df_hp.columns)
gbcp

#### 11.2 UDF call

In [ ]:
f_df

In [ ]:
pd_df = f_df.filter(col("F_CODE") == "0307").filter(col("LAMBDA") < 0.002).filter(col("ALPHA") < 0.2).to_pandas()
pd_df.shape
pd_df["Y_BKP"] = pd_df["Y"]
pd_df["Y"] = np.log(pd_df["Y"])
#pd_df["TOTAL_SPENDS_OVERALL_LAG1"] = np.log(pd_df["TOTAL_SPENDS_OVERALL"])
pd_df["TOTAL_SPENDS_OVERALL_LAG1"] = pd_df["TOTAL_SPENDS_OVERALL"].shift(1).fillna(0)

#pd_df["TOTAL_SPENDS_OVERALL"] = np.log(pd_df["TOTAL_SPENDS_OVERALL"])
pd_df["TOTAL_SPENDS_OVERALL_LAG2"] = pd_df["TOTAL_SPENDS_OVERALL"].shift(2).fillna(0)

pd_df.head()

In [ ]:
pd_df["DS"] = pd.to_datetime(pd_df["DS"])
pd_df["ASP"] = 1

In [ ]:
get_forecast_UDF2(pd_df)

In [ ]:
from snowflake.snowpark.functions import log, col, ln
import math
# Suppose df is your Snowpark DataFrame
f_df = f_df.with_column("Y_BKP", col("Y"))
#f_df = f_df.with_column("Y", log(math.e, x = col("Y")))
f_df = f_df.with_column("Y", col("LOG_NO_OF_NEW_JOINEES"))

#f_df = f_df.with_column("TOTAL_SPENDS_OVERALL", ln(col("TOTAL_SPENDS_OVERALL") + 1))



In [ ]:
from snowflake.snowpark.window import Window
from snowflake.snowpark.functions import col, lag, coalesce, lit

w = Window.partition_by("F_CODE").order_by("DS")

f_df = f_df.with_column(
    "TOTAL_SPENDS_OVERALL_LAG1",
    lag(col("TOTAL_SPENDS_OVERALL"), 1).over(w)
)

f_df = f_df.with_column(
    "TOTAL_SPENDS_OVERALL_LAG1",
    coalesce(col("TOTAL_SPENDS_OVERALL_LAG1"), lit(0))
)

f_df = f_df.with_column(
    "TOTAL_SPENDS_OVERALL_LAG2",
    lag(col("TOTAL_SPENDS_OVERALL"), 2).over(w)
)

f_df = f_df.with_column(
    "TOTAL_SPENDS_OVERALL_LAG2",
    coalesce(col("TOTAL_SPENDS_OVERALL_LAG2"), lit(0))
)

In [ ]:
f_df = f_df.with_column("ASP", col("Y_BKP")/100)

In [ ]:
gbcp

In [ ]:
result_schema

In [ ]:
f_df

In [0]:
df_f = f_df.select(gbcp+["DS","Y","ASP"]+app_config['feature_selection']['exogenous_variables']['uncertain_corr']+app_config['feature_selection']['exogenous_variables']['positive_corr']+app_config['feature_selection']['exogenous_variables']['negative_corr']).group_by(gbcp).applyInPandas(get_forecast_UDF2, output_schema=result_schema, packages=["scikit-learn", "pandas", "numpy"])

In [ ]:
df_f

#### 11.3 Export LASSO results

In [ ]:
output_table_name_all_results = "DEPLOY_LASSO_MODELING_RESULTS_ALL_ITERS"
results_s_with_ts = df_f.with_column("LOAD_TS", F.current_timestamp())
results_s_with_ts.write.mode("append").save_as_table(output_table_name_all_results)
print(results_s_with_ts.count())

In [ ]:
output_table_name_all_results = "DEPLOY_LASSO_MODELING_RESULTS_ALL_ITERS"

### 12. Post-processing - Coefficients & Contributions

In [ ]:
test_df = session.table(output_table_name_all_results)
print("All data ->", test_df.count())
latest_ts = test_df.select(F.max("LOAD_TS")).collect()[0][0]
latest_data = test_df.filter(F.col("LOAD_TS") == F.lit(latest_ts))
print("Latest data ->", latest_data.count())

In [0]:
merged_lasso_results = latest_data

POSWeekStartDate Iteration_ID Product UPC contributions model_coefficients status 2023-01-02 62600293398_0.1_0.002915 62600293398 {'POSWeekStartDate': '2023-01-02', 'ACV_contribution_base': 85.21058308783705, 'CATEGORY_CLUSTER_si_weekly_contribution_base': 0.22748871293475803, 'Intercept_contribution_base': 105.32681163031698, 'Predicted_sales': 87.54512122749301, 'TPR_finalized_contribution_impact': 0.0, 'good_friday_contribution_impact': 0.0, 'internalComp1_TPR_contribution_base': 0.0, 'labor_day_contribution_impact': 0.0, 'log_median_baseprice_finalized_contribution_base': -100.13397979736328, 'national_day_for_truth_and_reconciliation_contribution_impact': 0.0, 'trend_year_contribution_base': -3.0858113863147794, 'victoria_day_contribution_impact': 0.0, 'Comp': 0.0, 'Incremental': 0.0, 'Base': 87.54509224741074, 'Adj_Base': 87.54509224741074, 'Final_Base': 87.54509224741074, 'Final_Incremental': 0.0, 'Lift': 0.0, 'Year': 2023, 'Iteration_ID': '62600293398_0.1_0.002915'} {'Product UPC': {0: '62600293398', 1: '62600293398', 2: '62600293398', 3: '62600293398', 4: '62600293398', 5: '62600293398', 6: '62600293398', 7: '62600293398', 8: '62600293398', 9: '62600293398', 10: '62600293398'}, 'Parameters': {0: 'Intercept', 1: 'national_day_for_truth_and_reconciliation', 2: 'victoria_day', 3: 'CATEGORY_CLUSTER_si_weekly', 4: 'TPR_finalized', 5: 'labor_day', 6: 'good_friday', 7: 'trend_year', 8: 'log_median_baseprice_finalized', 9: 'internalComp1_TPR', 10: 'ACV'}, 'Value': {0: 4.657068008099942, 1: 0.9106727056798931, 2: 0.034725790697172416, 3: 0.1381756343099891, 4: 0.0243126421381609, 5: 0.26270769896738044, 6: 0.4251416253453728, 7: -0.9020034665984071, 8: -1.1647797593270006, 9: -0.01356358868498837, 10: 3.6619091242760202}, 'mape': {0: 50.49670161832608, 1: 50.49670161832608, 2: 50.49670161832608, 3: 50.49670161832608, 4: 50.49670161832608, 5: 50.49670161832608, 6: 50.49670161832608, 7: 50.49670161832608, 8: 50.49670161832608, 9: 50.49670161832608, 10: 50.49670161832608}, 'wmape': {0: 0.4217531101526417, 1: 0.4217531101526417, 2: 0.4217531101526417, 3: 0.4217531101526417, 4: 0.4217531101526417, 5: 0.4217531101526417, 6: 0.4217531101526417, 7: 0.4217531101526417, 8: 0.4217531101526417, 9: 0.4217531101526417, 10: 0.4217531101526417}, 'bias': {0: 6.215393071577785, 1: 6.215393071577785, 2: 6.215393071577785, 3: 6.215393071577785, 4: 6.215393071577785, 5: 6.215393071577785, 6: 6.215393071577785, 7: 6.215393071577785, 8: 6.215393071577785, 9: 6.215393071577785, 10: 6.215393071577785}, 'tracking_signal': {0: 26.928105646605992, 1: 26.928105646605992, 2: 26.928105646605992, 3: 26.928105646605992, 4: 26.928105646605992, 5: 26.928105646605992, 6: 26.928105646605992, 7: 26.928105646605992, 8: 26.928105646605992, 9: 26.928105646605992, 10: 26.928105646605992}, 'mae': {0: 20.542476720420332, 1: 20.542476720420332, 2: 20.542476720420332, 3: 20.542476720420332, 4: 20.542476720420332, 5: 20.542476720420332, 6: 20.542476720420332, 7: 20.542476720420332, 8: 20.542476720420332, 9: 20.542476720420332, 10: 20.542476720420332}, 'rmse': {0: 44.43975171821768, 1: 44.43975171821768, 2: 44.43975171821768, 3: 44.43975171821768, 4: 44.43975171821768, 5: 44.43975171821768, 6: 44.43975171821768, 7: 44.43975171821768, 8: 44.43975171821768, 9: 44.43975171821768, 10: 44.43975171821768}, 'smape': {0: 37.49366341410835, 1: 37.49366341410835, 2: 37.49366341410835, 3: 37.49366341410835, 4: 37.49366341410835, 5: 37.49366341410835, 6: 37.49366341410835, 7: 37.49366341410835, 8: 37.49366341410835, 9: 37.49366341410835, 10: 37.49366341410835}, 'rsq': {0: 0.6783892019254472, 1: 0.6783892019254472, 2: 0.6783892019254472, 3: 0.6783892019254472, 4: 0.6783892019254472, 5: 0.6783892019254472, 6: 0.6783892019254472, 7: 0.6783892019254472, 8: 0.6783892019254472, 9: 0.6783892019254472, 10: 0.6783892019254472}, 'status': {0: 'success', 1: 'success', 2: 'success', 3: 'success', 4: 'success', 5: 'success', 6: 'success', 7: 'success', 8: 'success', 9: 'success', 10: 'success'}, 'a

In [0]:
from snowflake.snowpark import functions as F

# Total no of products
total_prods = merged_lasso_results.select("F_CODE").distinct().count()
print("Total no of prods", total_prods)

# Filter: status == 'success'
merged_lasso_results = merged_lasso_results.filter(F.col("status") == "success")
success_prods = merged_lasso_results.select("F_CODE").distinct().count()
print("No of products without error", success_prods)

# Filter: contributions != 'None'
merged_lasso_results = merged_lasso_results.filter(F.col("contributions") != "None")
contrib_prods = merged_lasso_results.select("F_CODE").distinct().count()
print("No of products with contributions", contrib_prods)

Total no of prods 10
No of products without error 9
No of products with contributions 9


In [ ]:
df_json = (
    merged_lasso_results
    .select("model_coefficients")
    .distinct()
    .filter(F.col("model_coefficients").is_not_null() & (F.col("model_coefficients") != ""))
    .with_column(
        "model_coefficients_json",
        F.regexp_replace(F.col("model_coefficients"), "'", '"')   # convert pseudo-dict to JSON
    )
    .select("model_coefficients_json")
)

In [ ]:
df_json

In [ ]:
import re
from snowflake.snowpark import functions as F

def fix_json_keys(s: str) -> str:
    if s is None:
        return None

    # 1. Replace single quotes → double quotes
    s = s.replace("'", '"')

    # 2. Add quotes around unquoted keys:
    #    matches:   {key:   →   {"key":
    s = re.sub(r'([{,]\s*)([A-Za-z0-9_]+)\s*:', r'\1"\2":', s)

    return s

# Register UDF
fix_json_udf = session.udf.register(fix_json_keys, return_type=StringType(), input_types=[StringType()])


In [ ]:
df_fixed = (
    merged_lasso_results
    .select("model_coefficients")
    .distinct()
    .filter(F.col("model_coefficients").is_not_null() & (F.col("model_coefficients") != ""))
    .with_column("json_cleaned", fix_json_udf("model_coefficients"))
)

In [ ]:
df_fixed

In [ ]:

#parsed_schema = MapType(StringType(), MapType(StringType(), StringType()))
# define the map schema
from snowflake.snowpark import functions as F
from snowflake.snowpark.types import MapType, StringType
nested_map = MapType(StringType(), MapType(StringType(), StringType()))

# df_parsed = df_fixed.with_column(
#     "parsed",
#     F.parse_json(F.col("JSON_CLEANED"))
# )

df_parsed = (
    df_fixed
    .with_column("parsed_variant", F.parse_json(F.col("JSON_CLEANED")))
    .with_column("parsed", F.col("parsed_variant").cast(nested_map))
)

In [ ]:
df_parsed

In [ ]:

top_keys_df = (
    df_parsed
    .select(F.explode(F.object_keys(F.col("PARSED"))).alias("K"))
    .distinct()
)

top_keys = [r["K"].replace('"','') for r in top_keys_df.collect()]


In [ ]:
top_keys

In [ ]:
for key in top_keys:
    df_parsed = df_parsed.with_column(key, F.col("PARSED")[key])

In [ ]:
df_parsed

In [ ]:
df_flat = df_parsed.with_column(
    "idx",
    F.explode(F.object_keys(F.col("Parameters")))
)

df_flat

In [ ]:
df_flat.select(col("alpha"))

In [ ]:
for key in top_keys:
    print(key)
    df_flat = df_flat.with_column(
        key,
       F.get(F.col("parsed")[key], F.col("idx"))
    )


df_flat

In [ ]:

# 7. Drop parsed map and index if not needed
coef_df = df_flat.drop("PARSED", "IDX","MODEL_COEFFICIENTS","JSON_CLEANED","PARSED_VARIANT")

coef_df

In [ ]:
from snowflake.snowpark.functions import col, regexp_replace

#df_clean = coef_df

# Find all VARCHAR/STRING columns
# string_cols = [
#     field.name
#     for field in coef_df.schema.fields
#     if field.datatype.__class__.__name__.upper() in ("VARCHAR", "STRING", "TEXT")
# ]
# string_cols = ["F_CODE","ITERATION_ID","PARAMETERS","STATUS"]

string_cols = ["ITERATION_ID","STATUS","PARAMETERS"] + modeling_granularity_conf
float_cols = [column for column in coef_df.columns if column not in string_cols]

for c in float_cols:
    coef_df = coef_df.with_column(c, col(c).cast("FLOAT"))

for c in string_cols:
    coef_df = coef_df.with_column(c, col(c).cast("STRING"))
    
for c in string_cols:
    coef_df = coef_df.with_column(c, regexp_replace(col(c), '"', ''))
coef_df

In [ ]:
string_cols

In [ ]:
coef_df.schema.fields

In [ ]:
df_parsed

In [0]:
cont_df_raw = merged_lasso_results[['ITERATION_ID','START_OF_WEEK','CONTRIBUTIONS']].dropDuplicates()

In [ ]:
cont_df_raw

In [ ]:
from snowflake.snowpark.functions import col, regexp_replace, to_variant, parse_json, get, get_path
from snowflake.snowpark import Session
import ast, json

In [ ]:
df_clean = (
    cont_df_raw
        .with_column("contributions", regexp_replace(col("contributions"), "nan", "0"))
        .with_column("contributions", regexp_replace(col("contributions"), "inf,", "0,"))
)


In [ ]:
from snowflake.snowpark.functions import udf

@udf
def convert_to_json(py_dict_str: str) -> str:
    if py_dict_str is None:
        return None
    try:
        return json.dumps(ast.literal_eval(py_dict_str))
    except:
        return None

df_json = df_clean.with_column(
    "contributions_json",
    convert_to_json(col("contributions"))
)


In [ ]:
df_parsed = df_json.with_column(
    "parsed",
    parse_json(col("contributions_json"))
)


In [ ]:
df_parsed

In [ ]:
from snowflake.snowpark.functions import parse_json, object_keys, col, lit
from snowflake.snowpark import Session

# `sess` is your Snowpark session, `df` is your DataFrame, and
# 'dict_col' is the column that holds the dictionary-as-string.

# 0. (Optional) If your strings are python-dict-like (single quotes etc),
#    first normalize them to proper JSON (you likely already did this).
#    If needed, register a simple UDF convert_to_json(...) that uses ast.literal_eval + json.dumps.

# 1. Parse into a VARIANT column
df_parsed = df_json.with_column(
    "parsed",
    parse_json(col("contributions_json"))
)


# 2. Collect arrays of keys from all rows (OBJECT_KEYS returns an ARRAY)
keys_rows = df_parsed.select(object_keys(col("parsed")).alias("keys")).collect()
print(keys_rows)



In [ ]:
unique_keys = set()

# 3. Properly convert Variant to Python list
for row in keys_rows:
    arr = row["KEYS"]

    if arr is None:
        continue

    # If arr is a string like "['A','B']", convert it to list
    if isinstance(arr, str):
        arr = json.loads(arr.replace("'", '"'))

    # Now arr is a proper Python list
    for k in arr:
        unique_keys.add(str(k))

unique_keys_list = sorted(unique_keys)

In [ ]:
unique_keys_list

In [ ]:
df_parsed

In [ ]:
for k in unique_keys_list:
    print(k)
    df_parsed = df_parsed.with_column(k, F.col("parsed")[k]) 



In [ ]:
df_parsed

In [ ]:
cont_df = df_parsed.select(unique_keys_list)
cont_df

In [ ]:
cont_df.select("DS").limit(1).collect()[0][0]

In [ ]:
from snowflake.snowpark.functions import col, regexp_replace

#df_clean = coef_df

# # Find all VARCHAR/STRING columns
# string_cols = [
#     field.name
#     for field in coef_df.schema.fields
#     if field.datatype.__class__.__name__.upper() in ("VARCHAR", "STRING", "TEXT")
# ]
string_cols = ["ITERATION_ID"]
date_cols = ["DS"]

float_cols = [column for column in cont_df.columns if column not in string_cols + date_cols]

for c in date_cols:
    cont_df = cont_df.with_column(c, col(c).cast("TIMESTAMP"))
    
for c in float_cols:
    cont_df = cont_df.with_column(c, col(c).cast("FLOAT"))

for c in string_cols:
    cont_df = cont_df.with_column(c, col(c).cast("STRING"))
    
for c in string_cols:
    cont_df = cont_df.with_column(c, regexp_replace(col(c), '"', ''))
cont_df

#### 12.1 Export coefficients & contributions separately

In [ ]:
# # write_file(pos, algo_path, "/Pos_standardization_results (")
output_table_name_coeff = "DEPLOY_LASSO_COEFFICIENTS_ALL_ITERS_WEIGHTED"
results_s_with_ts = coef_df.with_column("LOAD_TS", F.current_timestamp())
results_s_with_ts.write.mode("overwrite").save_as_table(output_table_name_coeff)
print(results_s_with_ts.count())

In [ ]:
# # write_file(pos, algo_path, "/Pos_standardization_results (")
output_table_name_cont = "DEPLOY_LASSO_CONTRIBUTIONS_ALL_ITERS_WEIGHTED"
results_s_with_ts = cont_df.with_column("LOAD_TS", F.current_timestamp())
results_s_with_ts.write.mode("overwrite").save_as_table(output_table_name_cont)
print(results_s_with_ts.count())